# Grid Search for Wine Quality Red dataset

In [2]:
# Load required libraries
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data

import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split

Halving learnig rates after 15.000 iterations.

In [3]:
# Set seed
np.random.seed(8)
torch.manual_seed(8)

# Load Boston Housing dataset
wine_quality = np.genfromtxt('data/winequality-red.csv', delimiter=";")[1:,:]
target = wine_quality[:,-1].reshape(-1,1)
data = wine_quality[:,:-1]

# Split into training, validation and test set
X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=150, random_state=8)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=150, random_state=8)

# Convert arrays to Torch tensors
X_train = torch.FloatTensor(X_train)
y_train = torch.FloatTensor(y_train).view(-1,1)
X_val = torch.FloatTensor(X_val)
y_val = torch.FloatTensor(y_val).view(-1,1)
X_test = torch.FloatTensor(X_test)
y_test = torch.FloatTensor(y_test).view(-1,1)

# Normalise the training dataset
X_train_mean = X_train.mean(0)
X_train_std = X_train.std(0)
X_train_norm = X_train.add(-1, X_train_mean) / X_train_std
y_train_mean = torch.mean(y_train)
y_train_std = torch.std(y_train)
y_train_norm = y_train.add(-1, y_train_mean) / y_train_std

# Define the data-loader
train_data = torch.utils.data.TensorDataset(X_train_norm, y_train_norm)
train_loader = torch.utils.data.DataLoader(train_data, batch_size=32, num_workers=0)
val_data = torch.utils.data.TensorDataset(X_val, y_val)
val_loader = torch.utils.data.DataLoader(val_data, batch_size=150)
test_data = torch.utils.data.TensorDataset(X_test, y_test)
test_loader = torch.utils.data.DataLoader(test_data, batch_size=150)

In [4]:
# Fully connected Feed-Forward network with 2 hidden layers and SELU activations
if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

class Model(nn.Module):

    def __init__(self):
        super(Model, self).__init__()
        self.model = nn.Sequential(
                      nn.Linear(11, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50,1, bias=True)
                    ).to(device)


    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = self.model(x)
        return x

In [5]:
class evaluation(object):
    def __init__(self, test_data, n_samples, X_mean=None, X_std=None, y_mean=None, y_std=None):
        self.test_data = test_data
        self.X_mean = X_mean
        self.X_std = X_std
        self.y_mean = y_mean
        self.y_std = y_std
        self.n = 0
        self.avg_prediction = 0.
        self.sum_pp = 0.
        self.sumsqr_pp = 0.
        self.preds = torch.zeros(len(test_data.dataset),n_samples)

    def fn(self, model):

        with torch.autograd.no_grad():
            self.n += 1
            for x, y in iter(self.test_data):
                x = x.view(x.size(0), -1)

                if (self.X_mean is not None) & (self.X_std is not None):
                    x = (x - self.X_mean).float() / self.X_std

                standard_pred = model(x)

                if (self.y_mean is not None) & (self.y_std is not None):
                    standard_pred = standard_pred * self.y_std + self.y_mean
                
                self.preds[:,self.n-1] = standard_pred.view(-1,)
                self.avg_prediction = self.avg_prediction * (self.n - 1.) / self.n + standard_pred.view(-1,1) / self.n
                self.sum_pp += standard_pred
                self.sumsqr_pp += standard_pred * standard_pred
                std_pred = torch.sqrt((self.sumsqr_pp - (self.sum_pp * self.sum_pp) / self.n) / (self.n - 1))



                norm = torch.distributions.normal.Normal(y, std_pred)
                test_ll = norm.log_prob(self.avg_prediction).mean()



                error = nn.MSELoss(size_average=True)
                rmse = error(self.avg_prediction, y) ** 0.5

                return rmse, test_ll

## SGLD

In [16]:
# Load required libraries
import torch
import torchvision

from torch import nn
import torch.nn.functional as F
import numpy as np

import sgld
import model

# Set seed
np.random.seed(8)
torch.manual_seed(8)


# Network hyperparameters
lambda_ = 1.
# learning_rates = [9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6, 9e-7, 8e-7]
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
learning_rates = [9e-5, 8e-5, 7e-5, 6e-5, 5e-5, 4e-5, 3e-5, 2e-5, 1e-5, 9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6]
batch_size = 32.
dataset_size= 1299
# Number of samples to draw from the posterior distribution
n_samples = 300

# Initialise result array
val_llSGLD = np.zeros((1,len(learning_rates)))



for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = sgld.optim.sgld(network, lr, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
        
        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()



                running_loss += loss * batch_size / dataset_size

                # Sample from the posterior distribution
                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 0 - loss: 12.0236
lr 0.00009000 - epoch 1 - loss: 11.4945
lr 0.00009000 - epoch 2 - loss: 11.6240
lr 0.00009000 - epoch 3 - loss: 11.6325
lr 0.00009000 - epoch 4 - loss: 11.9154
lr 0.00009000 - epoch 5 - loss: 11.9546
lr 0.00009000 - epoch 6 - loss: 12.0089
lr 0.00009000 - epoch 7 - loss: 12.1039


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 8 - loss: 12.6775
lr 0.00009000 - epoch 9 - loss: 12.6369
lr 0.00009000 - epoch 10 - loss: 13.3761
lr 0.00009000 - epoch 11 - loss: 14.3392
lr 0.00009000 - epoch 12 - loss: 13.7969
lr 0.00009000 - epoch 13 - loss: 14.5321
lr 0.00009000 - epoch 14 - loss: 13.6576
lr 0.00009000 - epoch 15 - loss: 15.7990
lr 0.00009000 - epoch 16 - loss: 14.7731
lr 0.00009000 - epoch 17 - loss: 15.2267
lr 0.00009000 - epoch 18 - loss: 17.8866
lr 0.00009000 - epoch 19 - loss: nan
lr 0.00009000 - epoch 20 - loss: nan
lr 0.00009000 - epoch 21 - loss: nan
lr 0.00009000 - epoch 22 - loss: nan
lr 0.00009000 - epoch 23 - loss: nan
lr 0.00009000 - epoch 24 - loss: nan
lr 0.00009000 - epoch 25 - loss: nan
lr 0.00009000 - epoch 26 - loss: nan
lr 0.00009000 - epoch 27 - loss: nan
lr 0.00009000 - epoch 28 - loss: nan
lr 0.00009000 - epoch 29 - loss: nan
lr 0.00009000 - epoch 30 - loss: nan
lr 0.00009000 - epoch 31 - loss: nan
lr 0.00009000 - epoch 32 - loss: nan
lr 0.00009000 - epoch 33 - loss: 

lr 0.00009000 - epoch 225 - loss: nan
lr 0.00009000 - epoch 226 - loss: nan
lr 0.00009000 - epoch 227 - loss: nan
lr 0.00009000 - epoch 228 - loss: nan
lr 0.00009000 - epoch 229 - loss: nan
lr 0.00009000 - epoch 230 - loss: nan
lr 0.00009000 - epoch 231 - loss: nan
lr 0.00009000 - epoch 232 - loss: nan
lr 0.00009000 - epoch 233 - loss: nan
lr 0.00009000 - epoch 234 - loss: nan
lr 0.00009000 - epoch 235 - loss: nan
lr 0.00009000 - epoch 236 - loss: nan
lr 0.00009000 - epoch 237 - loss: nan
lr 0.00009000 - epoch 238 - loss: nan
lr 0.00009000 - epoch 239 - loss: nan
lr 0.00009000 - epoch 240 - loss: nan
lr 0.00009000 - epoch 241 - loss: nan
lr 0.00009000 - epoch 242 - loss: nan
lr 0.00009000 - epoch 243 - loss: nan
lr 0.00009000 - epoch 244 - loss: nan
lr 0.00009000 - epoch 245 - loss: nan
lr 0.00009000 - epoch 246 - loss: nan
lr 0.00009000 - epoch 247 - loss: nan
lr 0.00009000 - epoch 248 - loss: nan
lr 0.00009000 - epoch 249 - loss: nan
lr 0.00009000 - epoch 250 - loss: nan
lr 0.0000900

...

lr 0.00000100 - epoch 1683 - loss: 8.6707
lr 0.00000100 - epoch 1684 - loss: 8.6814
lr 0.00000100 - epoch 1685 - loss: 8.6820
lr 0.00000100 - epoch 1686 - loss: 8.6295
lr 0.00000100 - epoch 1687 - loss: 8.6279
lr 0.00000100 - epoch 1688 - loss: 8.6246
lr 0.00000100 - epoch 1689 - loss: 8.6182
lr 0.00000100 - epoch 1690 - loss: 8.5957
lr 0.00000100 - epoch 1691 - loss: 8.5887
lr 0.00000100 - epoch 1692 - loss: 8.5857
lr 0.00000100 - epoch 1693 - loss: 8.5849
lr 0.00000100 - epoch 1694 - loss: 8.5809
lr 0.00000100 - epoch 1695 - loss: 8.5603
lr 0.00000100 - epoch 1696 - loss: 8.5725
lr 0.00000100 - epoch 1697 - loss: 8.5810
lr 0.00000100 - epoch 1698 - loss: 8.5420
lr 0.00000100 - epoch 1699 - loss: 8.5634
lr 0.00000100 - epoch 1700 - loss: 8.6084
lr 0.00000100 - epoch 1701 - loss: 8.5975
lr 0.00000100 - epoch 1702 - loss: 8.6247
lr 0.00000100 - epoch 1703 - loss: 8.5946
lr 0.00000100 - epoch 1704 - loss: 8.6100
lr 0.00000100 - epoch 1705 - loss: 8.5981
lr 0.00000100 - epoch 1706 - loss:

lr 0.00000100 - epoch 1879 - loss: 8.4867
lr 0.00000100 - epoch 1880 - loss: 8.4791
lr 0.00000100 - epoch 1881 - loss: 8.4925
lr 0.00000100 - epoch 1882 - loss: 8.4704
lr 0.00000100 - epoch 1883 - loss: 8.4694
lr 0.00000100 - epoch 1884 - loss: 8.4757
lr 0.00000100 - epoch 1885 - loss: 8.4791
lr 0.00000100 - epoch 1886 - loss: 8.4685
lr 0.00000100 - epoch 1887 - loss: 8.4472
lr 0.00000100 - epoch 1888 - loss: 8.4487
lr 0.00000100 - epoch 1889 - loss: 8.4600
lr 0.00000100 - epoch 1890 - loss: 8.4692
lr 0.00000100 - epoch 1891 - loss: 8.4735
lr 0.00000100 - epoch 1892 - loss: 8.4713
lr 0.00000100 - epoch 1893 - loss: 8.4647
lr 0.00000100 - epoch 1894 - loss: 8.4565
lr 0.00000100 - epoch 1895 - loss: 8.4635
lr 0.00000100 - epoch 1896 - loss: 8.4506
lr 0.00000100 - epoch 1897 - loss: 8.4563
lr 0.00000100 - epoch 1898 - loss: 8.4424
lr 0.00000100 - epoch 1899 - loss: 8.4387
lr 0.00000100 - epoch 1900 - loss: 8.4609
lr 0.00000100 - epoch 1901 - loss: 8.4620
lr 0.00000100 - epoch 1902 - loss:

lr 0.00000100 - epoch 2077 - loss: 8.4881
lr 0.00000100 - epoch 2078 - loss: 8.4982
lr 0.00000100 - epoch 2079 - loss: 8.4956
lr 0.00000100 - epoch 2080 - loss: 8.4878
lr 0.00000100 - epoch 2081 - loss: 8.4867
lr 0.00000100 - epoch 2082 - loss: 8.4924
lr 0.00000100 - epoch 2083 - loss: 8.4994
lr 0.00000100 - epoch 2084 - loss: 8.4953
lr 0.00000100 - epoch 2085 - loss: 8.5011
lr 0.00000100 - epoch 2086 - loss: 8.5043
lr 0.00000100 - epoch 2087 - loss: 8.5039
lr 0.00000100 - epoch 2088 - loss: 8.5091
lr 0.00000100 - epoch 2089 - loss: 8.5284
lr 0.00000100 - epoch 2090 - loss: 8.5507
lr 0.00000100 - epoch 2091 - loss: 8.5623
lr 0.00000100 - epoch 2092 - loss: 8.5701
lr 0.00000100 - epoch 2093 - loss: 8.5670
lr 0.00000100 - epoch 2094 - loss: 8.5523
lr 0.00000100 - epoch 2095 - loss: 8.5330
lr 0.00000100 - epoch 2096 - loss: 8.5215
lr 0.00000100 - epoch 2097 - loss: 8.5157
lr 0.00000100 - epoch 2098 - loss: 8.5247
lr 0.00000100 - epoch 2099 - loss: 8.5483
lr 0.00000100 - epoch 2100 - loss:

lr 0.00000100 - epoch 2274 - loss: 8.5357
lr 0.00000100 - epoch 2275 - loss: 8.5579
lr 0.00000100 - epoch 2276 - loss: 8.5587
lr 0.00000100 - epoch 2277 - loss: 8.5514
lr 0.00000100 - epoch 2278 - loss: 8.5426
lr 0.00000100 - epoch 2279 - loss: 8.5325
lr 0.00000100 - epoch 2280 - loss: 8.5405
lr 0.00000100 - epoch 2281 - loss: 8.5389
lr 0.00000100 - epoch 2282 - loss: 8.5402
lr 0.00000100 - epoch 2283 - loss: 8.5378
lr 0.00000100 - epoch 2284 - loss: 8.5315
lr 0.00000100 - epoch 2285 - loss: 8.5327
lr 0.00000100 - epoch 2286 - loss: 8.5330
lr 0.00000100 - epoch 2287 - loss: 8.5429
lr 0.00000100 - epoch 2288 - loss: 8.5587
lr 0.00000100 - epoch 2289 - loss: 8.5672
lr 0.00000100 - epoch 2290 - loss: 8.5804
lr 0.00000100 - epoch 2291 - loss: 8.5788
lr 0.00000100 - epoch 2292 - loss: 8.5650
lr 0.00000100 - epoch 2293 - loss: 8.5889
lr 0.00000100 - epoch 2294 - loss: 8.5680
lr 0.00000100 - epoch 2295 - loss: 8.5547
lr 0.00000100 - epoch 2296 - loss: 8.5627
lr 0.00000100 - epoch 2297 - loss:

lr 0.00000100 - epoch 2471 - loss: 8.7091
lr 0.00000100 - epoch 2472 - loss: 8.6920
lr 0.00000100 - epoch 2473 - loss: 8.6768
lr 0.00000100 - epoch 2474 - loss: 8.6572
lr 0.00000100 - epoch 2475 - loss: 8.6571
lr 0.00000100 - epoch 2476 - loss: 8.6484
lr 0.00000100 - epoch 2477 - loss: 8.6444
lr 0.00000100 - epoch 2478 - loss: 8.6304
lr 0.00000100 - epoch 2479 - loss: 8.6182
lr 0.00000100 - epoch 2480 - loss: 8.6302
lr 0.00000100 - epoch 2481 - loss: 8.6329
lr 0.00000100 - epoch 2482 - loss: 8.6344
lr 0.00000100 - epoch 2483 - loss: 8.6323
lr 0.00000100 - epoch 2484 - loss: 8.6282
lr 0.00000100 - epoch 2485 - loss: 8.6229
lr 0.00000100 - epoch 2486 - loss: 8.6291
lr 0.00000100 - epoch 2487 - loss: 8.6308
lr 0.00000100 - epoch 2488 - loss: 8.6347
lr 0.00000100 - epoch 2489 - loss: 8.6294
lr 0.00000100 - epoch 2490 - loss: 8.6153
lr 0.00000100 - epoch 2491 - loss: 8.6167
lr 0.00000100 - epoch 2492 - loss: 8.6055
lr 0.00000100 - epoch 2493 - loss: 8.6161
lr 0.00000100 - epoch 2494 - loss:

In [8]:
val_llSGLD
# 3e-5
# 4e-5
# 3e-5

array([[         nan,          nan,          nan,          nan,
                 nan,          nan,  -1.07515228,  -1.70356905,
         -2.12391591,  -2.20465994,  -2.69242978,  -2.56819725,
         -3.60795736,  -3.37804031,  -3.31732154,  -4.95467424,
         -6.52039528, -17.82919502]])

## pSGLD

In [17]:
import torch
import torchvision
import os

from itertools import chain
from torch import nn
from torchvision import transforms
import torch.nn.functional as F
import numpy as np

import psgld 

np.random.seed(8)
torch.manual_seed(8)





lambda_ = 1.
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
learning_rates = [9e-2, 8e-2, 7e-2, 6e-2, 5e-2, 4e-2, 3e-2, 2e-2, 1e-2, 9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 3e-3, 2e-3, 1e-3]
# learning_rates = [1e-2, 9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 2e-3, 1e-3]
alpha = 0.99


batch_size = 32
dataset_size= 1299

n_chains = 10
n_samples = 300


val_llPSGLD = np.zeros((1,len(learning_rates)))


for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = psgld.optim.psgld(network, lr, alpha, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()


                running_loss += loss * batch_size / dataset_size


                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llPSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.09000000 - epoch 0 - loss: 7272253.0000
lr 0.09000000 - epoch 1 - loss: 8499.4561
lr 0.09000000 - epoch 2 - loss: 5048.0566
lr 0.09000000 - epoch 3 - loss: 3604.9255
lr 0.09000000 - epoch 4 - loss: 2664.9866
lr 0.09000000 - epoch 5 - loss: 1989.2311
lr 0.09000000 - epoch 6 - loss: 1591.7844
lr 0.09000000 - epoch 7 - loss: 1374.2253
lr 0.09000000 - epoch 8 - loss: 1234.5070


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.09000000 - epoch 9 - loss: 1164.0225
lr 0.09000000 - epoch 10 - loss: 1146.9153
lr 0.09000000 - epoch 11 - loss: 1201.9270
lr 0.09000000 - epoch 12 - loss: 1191.3069
lr 0.09000000 - epoch 13 - loss: 2304.8350
lr 0.09000000 - epoch 14 - loss: 716.2561
lr 0.09000000 - epoch 15 - loss: 530.3923
lr 0.09000000 - epoch 16 - loss: 352.2263
lr 0.09000000 - epoch 17 - loss: 413.3527
lr 0.09000000 - epoch 18 - loss: 241.9389
lr 0.09000000 - epoch 19 - loss: 252.0424
lr 0.09000000 - epoch 20 - loss: 204.7825
lr 0.09000000 - epoch 21 - loss: 186.1474
lr 0.09000000 - epoch 22 - loss: 117.3416
lr 0.09000000 - epoch 23 - loss: 77.1852
lr 0.09000000 - epoch 24 - loss: 67.9931
lr 0.09000000 - epoch 25 - loss: 58.0170
lr 0.09000000 - epoch 26 - loss: 34.5258
lr 0.09000000 - epoch 27 - loss: 27.3974
lr 0.09000000 - epoch 28 - loss: 23.1148
lr 0.09000000 - epoch 29 - loss: 18.6820
lr 0.09000000 - epoch 30 - loss: 20.7628
lr 0.09000000 - epoch 31 - loss: 14.2964
lr 0.09000000 - epoch 32 - loss: 14.342

lr 0.09000000 - epoch 205 - loss: 16.0048
lr 0.09000000 - epoch 206 - loss: 16.0184
lr 0.09000000 - epoch 207 - loss: 16.0346
lr 0.09000000 - epoch 208 - loss: 6893.3945
lr 0.09000000 - epoch 209 - loss: 84.7742
lr 0.09000000 - epoch 210 - loss: 3453.7629
lr 0.09000000 - epoch 211 - loss: 16.0572
lr 0.09000000 - epoch 212 - loss: 683.7507
lr 0.09000000 - epoch 213 - loss: 20.2824
lr 0.09000000 - epoch 214 - loss: 271.8461
lr 0.09000000 - epoch 215 - loss: 841.8029
lr 0.09000000 - epoch 216 - loss: 75.2302
lr 0.09000000 - epoch 217 - loss: 16.2514
lr 0.09000000 - epoch 218 - loss: 111569.9219
lr 0.09000000 - epoch 219 - loss: 604.4910
lr 0.09000000 - epoch 220 - loss: 17.6610
lr 0.09000000 - epoch 221 - loss: 16.0443
lr 0.09000000 - epoch 222 - loss: 19091.9922
lr 0.09000000 - epoch 223 - loss: 3439.0813
lr 0.09000000 - epoch 224 - loss: 2362.9697
lr 0.09000000 - epoch 225 - loss: 16.0804
lr 0.09000000 - epoch 226 - loss: 1087.1041
lr 0.09000000 - epoch 227 - loss: 2464.3391
lr 0.090000

...

lr 0.00100000 - epoch 1599 - loss: 8.8420
lr 0.00100000 - epoch 1600 - loss: 8.9307
lr 0.00100000 - epoch 1601 - loss: 8.8630
lr 0.00100000 - epoch 1602 - loss: 8.8887
lr 0.00100000 - epoch 1603 - loss: 8.8984
lr 0.00100000 - epoch 1604 - loss: 8.8193
lr 0.00100000 - epoch 1605 - loss: 8.9366
lr 0.00100000 - epoch 1606 - loss: 8.9808
lr 0.00100000 - epoch 1607 - loss: 8.7569
lr 0.00100000 - epoch 1608 - loss: 8.7731
lr 0.00100000 - epoch 1609 - loss: 8.7331
lr 0.00100000 - epoch 1610 - loss: 8.6534
lr 0.00100000 - epoch 1611 - loss: 8.8026
lr 0.00100000 - epoch 1612 - loss: 8.7576
lr 0.00100000 - epoch 1613 - loss: 8.6822
lr 0.00100000 - epoch 1614 - loss: 8.6638
lr 0.00100000 - epoch 1615 - loss: 8.7381
lr 0.00100000 - epoch 1616 - loss: 8.7669
lr 0.00100000 - epoch 1617 - loss: 8.9551
lr 0.00100000 - epoch 1618 - loss: 8.9635
lr 0.00100000 - epoch 1619 - loss: 9.1022
lr 0.00100000 - epoch 1620 - loss: 8.9264
lr 0.00100000 - epoch 1621 - loss: 9.0454
lr 0.00100000 - epoch 1622 - loss:

lr 0.00100000 - epoch 1796 - loss: 8.5800
lr 0.00100000 - epoch 1797 - loss: 8.5728
lr 0.00100000 - epoch 1798 - loss: 8.6302
lr 0.00100000 - epoch 1799 - loss: 8.6369
lr 0.00100000 - epoch 1800 - loss: 8.7274
lr 0.00100000 - epoch 1801 - loss: 8.7671
lr 0.00100000 - epoch 1802 - loss: 8.8628
lr 0.00100000 - epoch 1803 - loss: 9.0000
lr 0.00100000 - epoch 1804 - loss: 8.7317
lr 0.00100000 - epoch 1805 - loss: 8.6745
lr 0.00100000 - epoch 1806 - loss: 8.5182
lr 0.00100000 - epoch 1807 - loss: 8.6489
lr 0.00100000 - epoch 1808 - loss: 8.7524
lr 0.00100000 - epoch 1809 - loss: 8.8080
lr 0.00100000 - epoch 1810 - loss: 8.8361
lr 0.00100000 - epoch 1811 - loss: 8.8782
lr 0.00100000 - epoch 1812 - loss: 8.9703
lr 0.00100000 - epoch 1813 - loss: 8.7655
lr 0.00100000 - epoch 1814 - loss: 8.9044
lr 0.00100000 - epoch 1815 - loss: 8.7375
lr 0.00100000 - epoch 1816 - loss: 8.7316
lr 0.00100000 - epoch 1817 - loss: 8.7598
lr 0.00100000 - epoch 1818 - loss: 8.8250
lr 0.00100000 - epoch 1819 - loss:

lr 0.00100000 - epoch 1993 - loss: 9.2081
lr 0.00100000 - epoch 1994 - loss: 9.2942
lr 0.00100000 - epoch 1995 - loss: 9.1280
lr 0.00100000 - epoch 1996 - loss: 9.1332
lr 0.00100000 - epoch 1997 - loss: 9.1283
lr 0.00100000 - epoch 1998 - loss: 9.1849
lr 0.00100000 - epoch 1999 - loss: 9.1384
lr 0.00100000 - epoch 2000 - loss: 9.1364
lr 0.00100000 - epoch 2001 - loss: 9.1065
lr 0.00100000 - epoch 2002 - loss: 8.9293
lr 0.00100000 - epoch 2003 - loss: 8.9827
lr 0.00100000 - epoch 2004 - loss: 8.9616
lr 0.00100000 - epoch 2005 - loss: 9.0578
lr 0.00100000 - epoch 2006 - loss: 9.0695
lr 0.00100000 - epoch 2007 - loss: 9.1069
lr 0.00100000 - epoch 2008 - loss: 8.9407
lr 0.00100000 - epoch 2009 - loss: 8.9566
lr 0.00100000 - epoch 2010 - loss: 8.9927
lr 0.00100000 - epoch 2011 - loss: 9.0858
lr 0.00100000 - epoch 2012 - loss: 9.0067
lr 0.00100000 - epoch 2013 - loss: 8.8694
lr 0.00100000 - epoch 2014 - loss: 8.9070
lr 0.00100000 - epoch 2015 - loss: 8.9644
lr 0.00100000 - epoch 2016 - loss:

lr 0.00100000 - epoch 2189 - loss: 9.0087
lr 0.00100000 - epoch 2190 - loss: 8.9440
lr 0.00100000 - epoch 2191 - loss: 9.0547
lr 0.00100000 - epoch 2192 - loss: 9.0118
lr 0.00100000 - epoch 2193 - loss: 8.9248
lr 0.00100000 - epoch 2194 - loss: 8.9336
lr 0.00100000 - epoch 2195 - loss: 8.8552
lr 0.00100000 - epoch 2196 - loss: 8.8669
lr 0.00100000 - epoch 2197 - loss: 8.8188
lr 0.00100000 - epoch 2198 - loss: 8.8516
lr 0.00100000 - epoch 2199 - loss: 8.7445
lr 0.00100000 - epoch 2200 - loss: 8.8063
lr 0.00100000 - epoch 2201 - loss: 8.8412
lr 0.00100000 - epoch 2202 - loss: 8.9006
lr 0.00100000 - epoch 2203 - loss: 8.8793
lr 0.00100000 - epoch 2204 - loss: 8.8723
lr 0.00100000 - epoch 2205 - loss: 8.9082
lr 0.00100000 - epoch 2206 - loss: 8.8950
lr 0.00100000 - epoch 2207 - loss: 8.9191
lr 0.00100000 - epoch 2208 - loss: 8.7666
lr 0.00100000 - epoch 2209 - loss: 8.8573
lr 0.00100000 - epoch 2210 - loss: 8.9037
lr 0.00100000 - epoch 2211 - loss: 8.7875
lr 0.00100000 - epoch 2212 - loss:

lr 0.00100000 - epoch 2385 - loss: 8.9327
lr 0.00100000 - epoch 2386 - loss: 9.0743
lr 0.00100000 - epoch 2387 - loss: 9.0711
lr 0.00100000 - epoch 2388 - loss: 9.1979
lr 0.00100000 - epoch 2389 - loss: 9.2135
lr 0.00100000 - epoch 2390 - loss: 9.1058
lr 0.00100000 - epoch 2391 - loss: 9.2208
lr 0.00100000 - epoch 2392 - loss: 9.1412
lr 0.00100000 - epoch 2393 - loss: 9.0656
lr 0.00100000 - epoch 2394 - loss: 9.1858
lr 0.00100000 - epoch 2395 - loss: 9.1039
lr 0.00100000 - epoch 2396 - loss: 9.1123
lr 0.00100000 - epoch 2397 - loss: 9.1665
lr 0.00100000 - epoch 2398 - loss: 9.1524
lr 0.00100000 - epoch 2399 - loss: 9.1385
lr 0.00100000 - epoch 2400 - loss: 9.1316
lr 0.00100000 - epoch 2401 - loss: 9.1765
lr 0.00100000 - epoch 2402 - loss: 9.1468
lr 0.00100000 - epoch 2403 - loss: 9.1483
lr 0.00100000 - epoch 2404 - loss: 9.1680
lr 0.00100000 - epoch 2405 - loss: 9.2975
lr 0.00100000 - epoch 2406 - loss: 9.2416
lr 0.00100000 - epoch 2407 - loss: 9.2456
lr 0.00100000 - epoch 2408 - loss:

In [21]:
val_llPSGLD
#2e-2
# 9e-3
# 2e-2

array([[-12.18270016, -10.8288641 ,  -6.4278388 ,  -8.00785542,
         -7.95515442,  -3.02051187,  -1.82168901,  -1.43686998,
         -2.42570734,  -1.60817266,  -3.00902009,  -3.59309745,
         -3.75599194,  -3.98277187,  -4.00455379,  -4.12668562,
         -2.77889347,  -2.52000141]])

## K-SGLD

In [6]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgld


np.random.seed(8)
torch.manual_seed(8)



batch_size = 32
dataset_size=1299

n_chains = 10
n_samples = 300



# learning_rates = [1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
#5e-4
#6e-4
#2e-4
#8e-4]
# learning_rates = [1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4]
learning_rates = [9e-5, 8e-5, 7e-5, 6e-5, 5e-5, 4e-5, 3e-5, 2e-5, 1e-5, 9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6]


val_llKSGLD = np.zeros((1,len(learning_rates)))


for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgld.optim.KSGLD(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llKSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 0 - loss: 13.1944
lr 0.00009000 - epoch 1 - loss: 11.6554
lr 0.00009000 - epoch 2 - loss: 11.3719
lr 0.00009000 - epoch 3 - loss: 11.3161
lr 0.00009000 - epoch 4 - loss: 11.3201
lr 0.00009000 - epoch 5 - loss: 11.0920
lr 0.00009000 - epoch 6 - loss: 11.1275


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 7 - loss: 10.7743
lr 0.00009000 - epoch 8 - loss: 11.0219
lr 0.00009000 - epoch 9 - loss: 10.9508
lr 0.00009000 - epoch 10 - loss: 10.7847
lr 0.00009000 - epoch 11 - loss: 10.7090
lr 0.00009000 - epoch 12 - loss: 10.8244
lr 0.00009000 - epoch 13 - loss: 10.5800
lr 0.00009000 - epoch 14 - loss: 10.5512
lr 0.00009000 - epoch 15 - loss: 10.6367
lr 0.00009000 - epoch 16 - loss: 10.8814
lr 0.00009000 - epoch 17 - loss: 10.7098
lr 0.00009000 - epoch 18 - loss: 10.6767
lr 0.00009000 - epoch 19 - loss: 10.6133
lr 0.00009000 - epoch 20 - loss: 10.5491
lr 0.00009000 - epoch 21 - loss: 10.7105
lr 0.00009000 - epoch 22 - loss: 10.6557
lr 0.00009000 - epoch 23 - loss: 10.5130
lr 0.00009000 - epoch 24 - loss: 10.6144
lr 0.00009000 - epoch 25 - loss: 10.5299
lr 0.00009000 - epoch 26 - loss: 10.7504
lr 0.00009000 - epoch 27 - loss: 10.7318
lr 0.00009000 - epoch 28 - loss: 10.6451
lr 0.00009000 - epoch 29 - loss: 10.6555
lr 0.00009000 - epoch 30 - loss: 10.6120
lr 0.00009000 - epo

lr 0.00009000 - epoch 207 - loss: 10.0986
lr 0.00009000 - epoch 208 - loss: 9.9266
lr 0.00009000 - epoch 209 - loss: 9.9144
lr 0.00009000 - epoch 210 - loss: 9.6447
lr 0.00009000 - epoch 211 - loss: 10.0459
lr 0.00009000 - epoch 212 - loss: 9.5923
lr 0.00009000 - epoch 213 - loss: 9.2526
lr 0.00009000 - epoch 214 - loss: 9.4664
lr 0.00009000 - epoch 215 - loss: 10.0038
lr 0.00009000 - epoch 216 - loss: 9.7559
lr 0.00009000 - epoch 217 - loss: 9.5125
lr 0.00009000 - epoch 218 - loss: 9.2873
lr 0.00009000 - epoch 219 - loss: 10.2300
lr 0.00009000 - epoch 220 - loss: 9.8359
lr 0.00009000 - epoch 221 - loss: 9.9278
lr 0.00009000 - epoch 222 - loss: 10.0940
lr 0.00009000 - epoch 223 - loss: 9.4950
lr 0.00009000 - epoch 224 - loss: 9.3530
lr 0.00009000 - epoch 225 - loss: 9.7923
lr 0.00009000 - epoch 226 - loss: 9.5837
lr 0.00009000 - epoch 227 - loss: 9.2766
lr 0.00009000 - epoch 228 - loss: 9.4014
lr 0.00009000 - epoch 229 - loss: 9.1946
lr 0.00009000 - epoch 230 - loss: 9.4161
lr 0.000090

...

lr 0.00000100 - epoch 1617 - loss: 1.9367
lr 0.00000100 - epoch 1618 - loss: 1.9383
lr 0.00000100 - epoch 1619 - loss: 1.9334
lr 0.00000100 - epoch 1620 - loss: 1.9337
lr 0.00000100 - epoch 1621 - loss: 1.9335
lr 0.00000100 - epoch 1622 - loss: 1.9291
lr 0.00000100 - epoch 1623 - loss: 1.9294
lr 0.00000100 - epoch 1624 - loss: 1.9292
lr 0.00000100 - epoch 1625 - loss: 1.9315
lr 0.00000100 - epoch 1626 - loss: 1.9292
lr 0.00000100 - epoch 1627 - loss: 1.9317
lr 0.00000100 - epoch 1628 - loss: 1.9315
lr 0.00000100 - epoch 1629 - loss: 1.9304
lr 0.00000100 - epoch 1630 - loss: 1.9303
lr 0.00000100 - epoch 1631 - loss: 1.9315
lr 0.00000100 - epoch 1632 - loss: 1.9298
lr 0.00000100 - epoch 1633 - loss: 1.9280
lr 0.00000100 - epoch 1634 - loss: 1.9272
lr 0.00000100 - epoch 1635 - loss: 1.9281
lr 0.00000100 - epoch 1636 - loss: 1.9287
lr 0.00000100 - epoch 1637 - loss: 1.9298
lr 0.00000100 - epoch 1638 - loss: 1.9278
lr 0.00000100 - epoch 1639 - loss: 1.9296
lr 0.00000100 - epoch 1640 - loss:

lr 0.00000100 - epoch 1813 - loss: 1.8840
lr 0.00000100 - epoch 1814 - loss: 1.8878
lr 0.00000100 - epoch 1815 - loss: 1.8852
lr 0.00000100 - epoch 1816 - loss: 1.8850
lr 0.00000100 - epoch 1817 - loss: 1.8829
lr 0.00000100 - epoch 1818 - loss: 1.8848
lr 0.00000100 - epoch 1819 - loss: 1.8846
lr 0.00000100 - epoch 1820 - loss: 1.8826
lr 0.00000100 - epoch 1821 - loss: 1.8807
lr 0.00000100 - epoch 1822 - loss: 1.8814
lr 0.00000100 - epoch 1823 - loss: 1.8829
lr 0.00000100 - epoch 1824 - loss: 1.8808
lr 0.00000100 - epoch 1825 - loss: 1.8785
lr 0.00000100 - epoch 1826 - loss: 1.8769
lr 0.00000100 - epoch 1827 - loss: 1.8761
lr 0.00000100 - epoch 1828 - loss: 1.8776
lr 0.00000100 - epoch 1829 - loss: 1.8787
lr 0.00000100 - epoch 1830 - loss: 1.8763
lr 0.00000100 - epoch 1831 - loss: 1.8763
lr 0.00000100 - epoch 1832 - loss: 1.8773
lr 0.00000100 - epoch 1833 - loss: 1.8781
lr 0.00000100 - epoch 1834 - loss: 1.8758
lr 0.00000100 - epoch 1835 - loss: 1.8754
lr 0.00000100 - epoch 1836 - loss:

lr 0.00000100 - epoch 2009 - loss: 1.8495
lr 0.00000100 - epoch 2010 - loss: 1.8504
lr 0.00000100 - epoch 2011 - loss: 1.8517
lr 0.00000100 - epoch 2012 - loss: 1.8506
lr 0.00000100 - epoch 2013 - loss: 1.8494
lr 0.00000100 - epoch 2014 - loss: 1.8499
lr 0.00000100 - epoch 2015 - loss: 1.8489
lr 0.00000100 - epoch 2016 - loss: 1.8483
lr 0.00000100 - epoch 2017 - loss: 1.8491
lr 0.00000100 - epoch 2018 - loss: 1.8494
lr 0.00000100 - epoch 2019 - loss: 1.8488
lr 0.00000100 - epoch 2020 - loss: 1.8489
lr 0.00000100 - epoch 2021 - loss: 1.8496
lr 0.00000100 - epoch 2022 - loss: 1.8488
lr 0.00000100 - epoch 2023 - loss: 1.8467
lr 0.00000100 - epoch 2024 - loss: 1.8470
lr 0.00000100 - epoch 2025 - loss: 1.8488
lr 0.00000100 - epoch 2026 - loss: 1.8490
lr 0.00000100 - epoch 2027 - loss: 1.8469
lr 0.00000100 - epoch 2028 - loss: 1.8500
lr 0.00000100 - epoch 2029 - loss: 1.8503
lr 0.00000100 - epoch 2030 - loss: 1.8488
lr 0.00000100 - epoch 2031 - loss: 1.8499
lr 0.00000100 - epoch 2032 - loss:

lr 0.00000100 - epoch 2205 - loss: 1.8310
lr 0.00000100 - epoch 2206 - loss: 1.8286
lr 0.00000100 - epoch 2207 - loss: 1.8301
lr 0.00000100 - epoch 2208 - loss: 1.8285
lr 0.00000100 - epoch 2209 - loss: 1.8268
lr 0.00000100 - epoch 2210 - loss: 1.8267
lr 0.00000100 - epoch 2211 - loss: 1.8272
lr 0.00000100 - epoch 2212 - loss: 1.8254
lr 0.00000100 - epoch 2213 - loss: 1.8250
lr 0.00000100 - epoch 2214 - loss: 1.8252
lr 0.00000100 - epoch 2215 - loss: 1.8259
lr 0.00000100 - epoch 2216 - loss: 1.8246
lr 0.00000100 - epoch 2217 - loss: 1.8255
lr 0.00000100 - epoch 2218 - loss: 1.8272
lr 0.00000100 - epoch 2219 - loss: 1.8281
lr 0.00000100 - epoch 2220 - loss: 1.8276
lr 0.00000100 - epoch 2221 - loss: 1.8300
lr 0.00000100 - epoch 2222 - loss: 1.8294
lr 0.00000100 - epoch 2223 - loss: 1.8281
lr 0.00000100 - epoch 2224 - loss: 1.8280
lr 0.00000100 - epoch 2225 - loss: 1.8270
lr 0.00000100 - epoch 2226 - loss: 1.8272
lr 0.00000100 - epoch 2227 - loss: 1.8270
lr 0.00000100 - epoch 2228 - loss:

lr 0.00000100 - epoch 2401 - loss: 1.8151
lr 0.00000100 - epoch 2402 - loss: 1.8154
lr 0.00000100 - epoch 2403 - loss: 1.8169
lr 0.00000100 - epoch 2404 - loss: 1.8157
lr 0.00000100 - epoch 2405 - loss: 1.8170
lr 0.00000100 - epoch 2406 - loss: 1.8166
lr 0.00000100 - epoch 2407 - loss: 1.8167
lr 0.00000100 - epoch 2408 - loss: 1.8149
lr 0.00000100 - epoch 2409 - loss: 1.8153
lr 0.00000100 - epoch 2410 - loss: 1.8151
lr 0.00000100 - epoch 2411 - loss: 1.8149
lr 0.00000100 - epoch 2412 - loss: 1.8143
lr 0.00000100 - epoch 2413 - loss: 1.8151
lr 0.00000100 - epoch 2414 - loss: 1.8165
lr 0.00000100 - epoch 2415 - loss: 1.8144
lr 0.00000100 - epoch 2416 - loss: 1.8178
lr 0.00000100 - epoch 2417 - loss: 1.8175
lr 0.00000100 - epoch 2418 - loss: 1.8167
lr 0.00000100 - epoch 2419 - loss: 1.8176
lr 0.00000100 - epoch 2420 - loss: 1.8176
lr 0.00000100 - epoch 2421 - loss: 1.8171
lr 0.00000100 - epoch 2422 - loss: 1.8173
lr 0.00000100 - epoch 2423 - loss: 1.8164
lr 0.00000100 - epoch 2424 - loss:

In [7]:
val_llKSGLD
#9e-6
#2e-5

array([[ -1.2256788 ,  -1.53661144,  -1.2199018 ,  -1.58419812,
         -1.46843207,  -1.25581789,  -1.23317719,  -0.99482423,
         -1.13132048,  -1.17567265,  -1.48767138,  -1.86506534,
         -1.86810768,  -2.20539761,  -3.36781979,  -4.26315165,
         -7.36304665, -13.4564333 ]])

## K-SGFS

In [6]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgfs


np.random.seed(8)
torch.manual_seed(8)



batch_size = 32
dataset_size= 1299

n_chains = 10
n_samples = 300


# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5]
learning_rates = [9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 3e-3, 2e-3, 1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4, 4e-4, 3e-4, 2e-4, 1e-4]


val_llKSGFS = np.zeros((1,len(learning_rates)))

for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgfs.optim.KSGFS(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
#         val_resultsKSGFS[i,j] = rmse
        val_llKSGFS[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.00900000 - epoch 0 - loss: 11.9166
lr 0.00900000 - epoch 1 - loss: 10.9104
lr 0.00900000 - epoch 2 - loss: 10.5878
lr 0.00900000 - epoch 3 - loss: 10.4724
lr 0.00900000 - epoch 4 - loss: 10.3369
lr 0.00900000 - epoch 5 - loss: 10.1795
lr 0.00900000 - epoch 6 - loss: 10.1411


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00900000 - epoch 7 - loss: 10.0211
lr 0.00900000 - epoch 8 - loss: 10.0190
lr 0.00900000 - epoch 9 - loss: 10.0158
lr 0.00900000 - epoch 10 - loss: 9.9143
lr 0.00900000 - epoch 11 - loss: 9.8895
lr 0.00900000 - epoch 12 - loss: 9.9282
lr 0.00900000 - epoch 13 - loss: 9.8014
lr 0.00900000 - epoch 14 - loss: 9.7605
lr 0.00900000 - epoch 15 - loss: 9.7785
lr 0.00900000 - epoch 16 - loss: 9.8156
lr 0.00900000 - epoch 17 - loss: 9.8010
lr 0.00900000 - epoch 18 - loss: 9.7546
lr 0.00900000 - epoch 19 - loss: 9.6798
lr 0.00900000 - epoch 20 - loss: 9.6970
lr 0.00900000 - epoch 21 - loss: 9.7203
lr 0.00900000 - epoch 22 - loss: 9.6826
lr 0.00900000 - epoch 23 - loss: 9.6074
lr 0.00900000 - epoch 24 - loss: 9.6058
lr 0.00900000 - epoch 25 - loss: 9.5984
lr 0.00900000 - epoch 26 - loss: 9.6603
lr 0.00900000 - epoch 27 - loss: 9.5936
lr 0.00900000 - epoch 28 - loss: 9.5729
lr 0.00900000 - epoch 29 - loss: 9.5564
lr 0.00900000 - epoch 30 - loss: 9.5327
lr 0.00900000 - epoch 31 - loss: 9.4980


lr 0.00900000 - epoch 210 - loss: 7.7197
lr 0.00900000 - epoch 211 - loss: 7.6762
lr 0.00900000 - epoch 212 - loss: 7.7244
lr 0.00900000 - epoch 213 - loss: 7.6610
lr 0.00900000 - epoch 214 - loss: 7.6463
lr 0.00900000 - epoch 215 - loss: 7.7797
lr 0.00900000 - epoch 216 - loss: 7.7109
lr 0.00900000 - epoch 217 - loss: 7.6796
lr 0.00900000 - epoch 218 - loss: 7.7696
lr 0.00900000 - epoch 219 - loss: 7.6557
lr 0.00900000 - epoch 220 - loss: 7.6628
lr 0.00900000 - epoch 221 - loss: 7.5938
lr 0.00900000 - epoch 222 - loss: 7.6454
lr 0.00900000 - epoch 223 - loss: 7.5389
lr 0.00900000 - epoch 224 - loss: 7.5085
lr 0.00900000 - epoch 225 - loss: 7.6635
lr 0.00900000 - epoch 226 - loss: 7.6660
lr 0.00900000 - epoch 227 - loss: 7.5713
lr 0.00900000 - epoch 228 - loss: 7.6377
lr 0.00900000 - epoch 229 - loss: 7.5199
lr 0.00900000 - epoch 230 - loss: 7.6433
lr 0.00900000 - epoch 231 - loss: 7.6715
lr 0.00900000 - epoch 232 - loss: 7.6189
lr 0.00900000 - epoch 233 - loss: 7.5139
lr 0.00900000 - 

...

lr 0.00010000 - epoch 1622 - loss: 1.6369
lr 0.00010000 - epoch 1623 - loss: 1.5861
lr 0.00010000 - epoch 1624 - loss: 1.5944
lr 0.00010000 - epoch 1625 - loss: 1.6851
lr 0.00010000 - epoch 1626 - loss: 1.7324
lr 0.00010000 - epoch 1627 - loss: 1.6495
lr 0.00010000 - epoch 1628 - loss: 1.6407
lr 0.00010000 - epoch 1629 - loss: 1.6109
lr 0.00010000 - epoch 1630 - loss: 1.6261
lr 0.00010000 - epoch 1631 - loss: 1.6409
lr 0.00010000 - epoch 1632 - loss: 1.6768
lr 0.00010000 - epoch 1633 - loss: 1.6001
lr 0.00010000 - epoch 1634 - loss: 1.7586
lr 0.00010000 - epoch 1635 - loss: 1.7161
lr 0.00010000 - epoch 1636 - loss: 1.6390
lr 0.00010000 - epoch 1637 - loss: 1.6269
lr 0.00010000 - epoch 1638 - loss: 1.6418
lr 0.00010000 - epoch 1639 - loss: 1.6463
lr 0.00010000 - epoch 1640 - loss: 1.6826
lr 0.00010000 - epoch 1641 - loss: 1.7042
lr 0.00010000 - epoch 1642 - loss: 1.8242
lr 0.00010000 - epoch 1643 - loss: 1.7671
lr 0.00010000 - epoch 1644 - loss: 1.7789
lr 0.00010000 - epoch 1645 - loss:

lr 0.00010000 - epoch 1818 - loss: 1.6460
lr 0.00010000 - epoch 1819 - loss: 1.7425
lr 0.00010000 - epoch 1820 - loss: 1.7702
lr 0.00010000 - epoch 1821 - loss: 1.7808
lr 0.00010000 - epoch 1822 - loss: 1.6776
lr 0.00010000 - epoch 1823 - loss: 1.7006
lr 0.00010000 - epoch 1824 - loss: 1.6786
lr 0.00010000 - epoch 1825 - loss: 1.7413
lr 0.00010000 - epoch 1826 - loss: 1.6323
lr 0.00010000 - epoch 1827 - loss: 1.6758
lr 0.00010000 - epoch 1828 - loss: 1.6973
lr 0.00010000 - epoch 1829 - loss: 1.8030
lr 0.00010000 - epoch 1830 - loss: 1.7800
lr 0.00010000 - epoch 1831 - loss: 1.7704
lr 0.00010000 - epoch 1832 - loss: 1.7226
lr 0.00010000 - epoch 1833 - loss: 1.7565
lr 0.00010000 - epoch 1834 - loss: 1.7408
lr 0.00010000 - epoch 1835 - loss: 1.6653
lr 0.00010000 - epoch 1836 - loss: 1.7429
lr 0.00010000 - epoch 1837 - loss: 1.7681
lr 0.00010000 - epoch 1838 - loss: 1.7506
lr 0.00010000 - epoch 1839 - loss: 1.6980
lr 0.00010000 - epoch 1840 - loss: 1.6778
lr 0.00010000 - epoch 1841 - loss:

lr 0.00010000 - epoch 2014 - loss: 1.9106
lr 0.00010000 - epoch 2015 - loss: 1.8198
lr 0.00010000 - epoch 2016 - loss: 2.0112
lr 0.00010000 - epoch 2017 - loss: 1.9306
lr 0.00010000 - epoch 2018 - loss: 1.8587
lr 0.00010000 - epoch 2019 - loss: 1.9019
lr 0.00010000 - epoch 2020 - loss: 1.9191
lr 0.00010000 - epoch 2021 - loss: 1.8284
lr 0.00010000 - epoch 2022 - loss: 1.8196
lr 0.00010000 - epoch 2023 - loss: 1.9486
lr 0.00010000 - epoch 2024 - loss: 1.9029
lr 0.00010000 - epoch 2025 - loss: 1.9592
lr 0.00010000 - epoch 2026 - loss: 1.9787
lr 0.00010000 - epoch 2027 - loss: 1.9668
lr 0.00010000 - epoch 2028 - loss: 1.8352
lr 0.00010000 - epoch 2029 - loss: 1.9088
lr 0.00010000 - epoch 2030 - loss: 1.8636
lr 0.00010000 - epoch 2031 - loss: 1.8241
lr 0.00010000 - epoch 2032 - loss: 1.8722
lr 0.00010000 - epoch 2033 - loss: 1.8174
lr 0.00010000 - epoch 2034 - loss: 1.8909
lr 0.00010000 - epoch 2035 - loss: 1.8615
lr 0.00010000 - epoch 2036 - loss: 1.8197
lr 0.00010000 - epoch 2037 - loss:

lr 0.00010000 - epoch 2210 - loss: 1.9862
lr 0.00010000 - epoch 2211 - loss: 1.8892
lr 0.00010000 - epoch 2212 - loss: 1.9144
lr 0.00010000 - epoch 2213 - loss: 1.9362
lr 0.00010000 - epoch 2214 - loss: 1.9015
lr 0.00010000 - epoch 2215 - loss: 1.9639
lr 0.00010000 - epoch 2216 - loss: 1.9160
lr 0.00010000 - epoch 2217 - loss: 1.8470
lr 0.00010000 - epoch 2218 - loss: 1.9195
lr 0.00010000 - epoch 2219 - loss: 1.8726
lr 0.00010000 - epoch 2220 - loss: 1.8715
lr 0.00010000 - epoch 2221 - loss: 1.7935
lr 0.00010000 - epoch 2222 - loss: 1.8253
lr 0.00010000 - epoch 2223 - loss: 1.8341
lr 0.00010000 - epoch 2224 - loss: 1.8650
lr 0.00010000 - epoch 2225 - loss: 1.8088
lr 0.00010000 - epoch 2226 - loss: 1.8000
lr 0.00010000 - epoch 2227 - loss: 1.8330
lr 0.00010000 - epoch 2228 - loss: 1.8370
lr 0.00010000 - epoch 2229 - loss: 1.7216
lr 0.00010000 - epoch 2230 - loss: 1.8991
lr 0.00010000 - epoch 2231 - loss: 1.8800
lr 0.00010000 - epoch 2232 - loss: 1.8182
lr 0.00010000 - epoch 2233 - loss:

lr 0.00010000 - epoch 2406 - loss: 1.7017
lr 0.00010000 - epoch 2407 - loss: 1.8612
lr 0.00010000 - epoch 2408 - loss: 1.7643
lr 0.00010000 - epoch 2409 - loss: 1.7877
lr 0.00010000 - epoch 2410 - loss: 1.7648
lr 0.00010000 - epoch 2411 - loss: 1.8043
lr 0.00010000 - epoch 2412 - loss: 1.8647
lr 0.00010000 - epoch 2413 - loss: 1.7951
lr 0.00010000 - epoch 2414 - loss: 1.7693
lr 0.00010000 - epoch 2415 - loss: 1.8965
lr 0.00010000 - epoch 2416 - loss: 1.7885
lr 0.00010000 - epoch 2417 - loss: 1.7561
lr 0.00010000 - epoch 2418 - loss: 1.8009
lr 0.00010000 - epoch 2419 - loss: 1.7266
lr 0.00010000 - epoch 2420 - loss: 1.7303
lr 0.00010000 - epoch 2421 - loss: 1.7492
lr 0.00010000 - epoch 2422 - loss: 1.7097
lr 0.00010000 - epoch 2423 - loss: 1.7210
lr 0.00010000 - epoch 2424 - loss: 1.7527
lr 0.00010000 - epoch 2425 - loss: 1.6997
lr 0.00010000 - epoch 2426 - loss: 1.7910
lr 0.00010000 - epoch 2427 - loss: 1.8457
lr 0.00010000 - epoch 2428 - loss: 1.8252
lr 0.00010000 - epoch 2429 - loss:

In [7]:
val_llKSGFS
# 1e-3
# 7e-4

array([[-1.9193902 , -1.38121533, -1.47946656, -1.22547054, -1.65733433,
        -1.32165837, -1.45685196, -1.22069299, -0.95456684, -0.96285784,
        -0.98547232, -0.91941649, -1.02215123, -1.03140807, -1.23828828,
        -1.55713046, -1.72945678, -3.20034719]])